**IMPORT PACKAGE**

In [7]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import math
import statistics
from collections import OrderedDict

Setting Environtment

In [8]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

**DATA UNDERSTANDING**

In [9]:
df_raw = pd.read_csv('D:\\SKRIPSI\\Code\\Penilaian Mahasiswa.csv')

In [10]:
df_raw.head()

Nama  ID  Teori Bilangan  Aljabar Linear   Aplikasi Aljabar Linear   \
0  Responden1  A1               0                0                         5   
1  Responden2  A2               5                0                         5   
2  Responden3  A3               3                0                         4   
3  Responden4  A4               0                0                         4   
4  Responden5  A5               3                0                         0   

   Pengantar Desain Eksperimen   Perangkat Lunak Matematika   \
0                             0                            5   
1                             3                            0   
2                             0                            5   
3                             4                            5   
4                             0                            0   

   Praktikum Perangkat Lunak Matematika   Matematika Ekonomi dan Bisnis   \
0                                      5                               4   
1                                      0                               4   
2                                      5                               0   
3                                      5                               5   
4                                      0                               3   

   Persamaan Beda Hingga   Matematika Keuangan 1   Teori Grup Fuzzy   \
0                       5                       4                  0   
1                       4                       3                  4   
2                       0                       0                  0   
3                       0                       4                  4   
4                       0                       0                  3   

   Teori Grup Hingga   Pengantar Teori Graf   Kombinatorika   \
0                   0                      5               0   
1                   4                      5               0   
2                   0                      0               0   
3                   4                      0               0   
4                   4                      5               4   

   Sistem Basis Data   Praktikum Sistem Basis Data   Pengantar Biologi   \
0                   0                             0                   0   
1                   0                             0                   0   
2                   5                             5                   0   
3                   0                             0                   4   
4                   4                             4                   0   

   Pengantar Fisika   Pengantar Kimia   Pengantar Fungsi Univalen   \
0                  0                 0                           0   
1                  0                 0                           0   
2                  0                 0                           0   
3                  4                 0                           0   
4                  0                 0                           4   

   Matriks Atas Ring   Pengantar Teori Modul   Fungsi Khusus   \
0                   0                       4               0   
1                   0                       0               4   
2                   0                       3               3   
3                   0                       0               4   
4                   4                       3               4   

   Pengantar Sistem Dinamik Kontinu   Matematika Keuangan 2   \
0                                  4                       4   
1                                  0                       3   
2                                  0                       0   
3                                  4                       0   
4                                  4                       5   

   Pengantar Metode Peramalan   Pengantar Regresi Linear   \
0                            0                          0   
1                            5                          3   
2                            0       

In [11]:
df_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 152 entries, 0 to 151
Data columns (total 60 columns):
 #   Column                                              Non-Null Count  Dtype  
---  ------                                              --------------  -----  
 0   Nama                                                152 non-null    object 
 1   ID                                                  152 non-null    object 
 2   Teori Bilangan                                      152 non-null    int64  
 3   Aljabar Linear                                      152 non-null    int64  
 4   Aplikasi Aljabar Linear                             152 non-null    int64  
 5   Pengantar Desain Eksperimen                         152 non-null    int64  
 6   Perangkat Lunak Matematika                          152 non-null    int64  
 7   Praktikum Perangkat Lunak Matematika                152 non-null    int64  
 8   Matematika Ekonomi dan Bisnis                       152 non-null    int64  
 9  

In [12]:
df_raw.isna().sum()

Nama                                                  0
ID                                                    0
Teori Bilangan                                        0
Aljabar Linear                                        0
Aplikasi Aljabar Linear                               0
Pengantar Desain Eksperimen                           0
Perangkat Lunak Matematika                            0
Praktikum Perangkat Lunak Matematika                  0
Matematika Ekonomi dan Bisnis                         0
Persamaan Beda Hingga                                 0
Matematika Keuangan 1                                 0
Teori Grup Fuzzy                                      0
Teori Grup Hingga                                     0
Pengantar Teori Graf                                  0
Kombinatorika                                         0
Sistem Basis Data                                     0
Praktikum Sistem Basis Data                           0
Pengantar Biologi                               

In [13]:
df = df_raw.drop(['Nama','Waktu','Waktu dalam jam','ID'], axis=1)
df_2 = df_raw.drop(['Nama','Waktu','Waktu dalam jam','ID'], axis=1)

In [14]:
#cari nilai yang hanya 0 semuanya dari df
df_zero = df.loc[(df==0).all(axis=1)]
len(df_zero)

0

dapat dilihat hasil menunjukan bahwa semua responden telah mengambil minimal 1 mata kuliah pilihan

**PSS Calculation**

In [15]:
#Membuat Fungsi Proximity/Jarak
def Proximity(rating1,rating2):
    return 1-(1/(1+math.exp(-abs(rating1-rating2))))

#Membuat Fungsi Significance/Signifikansi
def Significance(rating1,rating2):
    range_rating = [1,2,3,4,5] #skala rating
    r_median = statistics.median(range_rating)
    return 1/(1+math.exp(-abs(rating1-r_median)*abs(rating2-r_median)))

#Membuat Fungsi Singularity/Singularitas
def Singularity(rating1,rating2, iterate):
    rata = df.iloc[:,iterate].mean()
    return 1-(1/(1+math.exp(-abs((rating1+rating2)/2-rata))))

**Heuristic Model Calculation**

In [16]:
#menhitung nilai PSS
def calculate_PSS_similarity(student_u, student_v):
    rating_student_u = df.loc[student_u] #mengambil data rating dari student u
    rating_student_v = df.loc[student_v] #mengambil data rating dari student v
    
    iterate = 0 #variabel untuk menghitung item ke berapa
    PSS = 0
    for col in rating_student_u.index:
        PSS += Proximity(rating_student_u[col], rating_student_v[col])*Significance(rating_student_u[col], rating_student_v[col])*Singularity(rating_student_u[col], rating_student_v[col], iterate)
        iterate = iterate + 1
    return PSS

#menhitung nilai Jaccaard
def calculate_Jaccard_similarity(student_u, student_v):
    rating_student_u = df.loc[student_u]
    rating_student_v = df.loc[student_v]

    items_u = set(rating_student_u.index[rating_student_u > 0]) #Memilih item yang pernah di nilai oleh user u
    items_v = set(rating_student_v.index[rating_student_v > 0]) #Memilih item yang pernah di nilai oleh user v
    intersection = len(items_u.intersection(items_v))
    union = len(items_u.union(items_v))
    return intersection/union

#menhitung nilai URP
def calculate_URP_similarity(student_u, student_v):
    rating_student_u = df.loc[student_u]
    rating_student_v = df.loc[student_v]
    
    mean_student_u = statistics.mean(rating_student_u)
    mean_student_v = statistics.mean(rating_student_v)
    
    var_student_u = statistics.variance(rating_student_u)
    var_student_v = statistics.variance(rating_student_v)
    return 1-(1/(1+math.exp(-abs(mean_student_u-mean_student_v)*abs(var_student_u-var_student_v))))

**PSS**

In [17]:
rating_student_u = df.loc[0]
rating_student_v = df.loc[1]

rating1 = rating_student_u[3]
rating2 = rating_student_v[3]

rata = df.iloc[:,3].mean()
singularity = 1-(1/(1+math.exp(-abs((rating1+rating2)/2-rata))))
print(singularity)
print(rata)

0.31511446043859004
0.7236842105263158


In [18]:
rows = [] #list untuk menyimpan data
students = df.index #mengambil index dari dataframe
for i in range(len(students)):
    row_data = [] #list untuk menyimpan data pada baris
    for j in range(len(students)):
        student1 = students[i]
        student2 = students[j]
        if student1 == student2:
            similarity = np.nan #similarity antara student dengan dirinya sendiri adalah NaN
        else: 
            similarity = calculate_PSS_similarity(student1, student2)
        row_data.append(similarity)
    rows.append(row_data)

df_pss = pd.DataFrame(rows)
df_pss.columns = students 
df_pss.index = students

df_pss

0         1         2         3         4         5         6    \
0         NaN  4.226505  5.104746  3.440622  2.125924  1.190659  1.640125   
1    4.226505       NaN  4.327212  3.430329  2.260211  1.047379  1.049735   
2    5.104746  4.327212       NaN  3.613811  2.168238  1.103858  1.317801   
3    3.440622  3.430329  3.613811       NaN  1.488632  0.686538  0.764917   
4    2.125924  2.260211  2.168238  1.488632       NaN  1.609129  1.630299   
5    1.190659  1.047379  1.103858  0.686538  1.609129       NaN  1.487549   
6    1.640125  1.049735  1.317801  0.764917  1.630299  1.487549       NaN   
7    1.446574  1.786117  1.427763  1.227850  1.282524  1.331802  1.252443   
8    1.475684  1.505784  1.391725  1.296517  0.813982  0.845407  0.832573   
9    2.300337  1.915249  2.262831  1.885035  0.848195  0.674767  0.706835   
10   2.425343  2.671578  3.163429  2.427774  1.180309  0.795894  0.762506   
11   3.083906  3.676837  3.408909  2.751442  1.628870  0.773532  0.800438   
12   3.508426  3.699493  3.767326  2.879187  2.207590  1.142406  1.246061   
13   3.247128  2.997173  3.100857  2.527308  2.237272  0.966676  1.204519   
14   2.803619  2.905151  2.698239  2.630599  1.652228  0.793942  1.088423   
15   2.207247  1.924555  2.335731  1.913088  1.054077  1.028249  1.325974   
16   4.394313  3.937239  4.760992  3.531263  2.264290  1.246369  1.409006   
17   4.647676  5.047897  4.941223  3.816126  2.382190  1.185853  1.506870   
18   4.705104  4.864992  4.805323  3.930740  2.364115  1.102606  1.487549   
19   4.796713  3.717515  5.371701  3.612210  2.183520  1.146411  1.309970   
20   4.887524  5.020973  4.799866  3.897022  2.153004  0.955563  1.244932   
21   4.643590  4.176462  4.973753  3.953940  2.001171  0.984649  1.096717   
22   4.614583  4.836309  4.591017  3.471957  2.232742  1.284223  1.449080   
23   4.413597  4.700709  4.257605  3.488994  2.089481  0.896181  1.317859   
24   4.722713  4.544046  4.718003  3.712963  1.977479  1.053876  1.327499   
25   5.298099  4.624883  5.548242  3.799981  2.271130  1.313986  1.680636   
26   1.815242  2.138055  1.947284  1.687895  1.285095  0.678065  0.721958   
27   4.689809  4.789783  5.065006  3.776326  2.171936  1.027480  1.292587   
28   4.671474  4.277881  5.291027  3.503737  2.255463  1.320203  1.625508   
29   5.380195  4.467393  5.646455  3.987651  2.578003  1.464317  1.691446   
30   4.767865  4.677406  5.078145  3.733667  2.230028  1.126986  1.549148   
31   4.224430  4.202699  4.913169  3.208738  2.287792  1.213698  1.269220   
32   1.725731  1.537610  1.964401  1.213749  1.407700  0.963293  0.990581   
33   4.622400  4.776524  4.963245  3.803504  2.316322  1.105825  1.323021   
34   5.069674  3.968304  5.335787  3.777788  2.521751  1.363056  1.665525   
35   4.935598  4.520494  5.168337  3.513373  2.439858  1.249759  1.667581   
36   4.993166  4.118511  5.497153  3.658619  2.377270  1.300548  1.609103   
37   5.105079  5.114769  5.060213  3.816928  2.376880  1.169451  1.586346   
38   4.943014  4.989047  5.213347  4.030715  2.308315  1.131423  1.434987   
39   4.850266  5.195647  4.600059  3.643353  2.412159  1.216445  1.471143   
40   4.409107  4.403548  4.709662  3.488281  1.991508  1.033904  1.210662   
41   4.556345  4.881116  5.018572  3.953183  1.977198  0.859011  1.199394   
42   3.823204  4.262437  4.453990  3.632114  1.825752  0.869068  1.101380   
43   4.365499  4.199816  4.917607  3.799991  2.467384  1.415829  1.652670   
44   4.694542  4.740403  4.759657  3.696966  1.832426  0.642201  0.943143   
45   5.221012  4.658180  5.599688  3.712233  2.432342  1.499029  1.707704   
46   4.697050  4.122951  5.466451  3.439067  2.342454  1.358197  1.634323   
47   5.078554  4.300548  5.574744  3.420787  2.207465  1.165600  1.567224   
48   4.956843  4.419369  5.600173  4.140515  2.431383  1.182281  1.476635   
49   4.783853  4.333749  5.397877  3.812625  2.454832  1.174285  1.337521   
50   4.608493  4.046870  5.072865  4.030487  2.031094  1.060483  1.289510   
51   5

In [19]:
rows = [] #list untuk menyimpan data
students = df.index #mengambil index dari dataframe
for i in range(len(students)):
    row_data = [] #list untuk menyimpan data pada baris
    for j in range(len(students)):
        student1 = students[i]
        student2 = students[j]
        if student1 == student2:
            similarity = np.nan #similarity antara student dengan dirinya sendiri adalah NaN
        else: 
            similarity = calculate_Jaccard_similarity(student1, student2)
        row_data.append(similarity)
    rows.append(row_data)

df_jaccard = pd.DataFrame(rows)
df_jaccard.columns = students 
df_jaccard.index = students

df_jaccard

0         1         2         3         4         5         6    \
0         NaN  0.322581  0.384615  0.285714  0.288889  0.320000  0.361702   
1    0.322581       NaN  0.193548  0.314286  0.372093  0.340000  0.300000   
2    0.384615  0.193548       NaN  0.205882  0.227273  0.240000  0.224490   
3    0.285714  0.314286  0.205882       NaN  0.312500  0.339623  0.301887   
4    0.288889  0.372093  0.227273  0.312500       NaN  0.826087  0.744681   
5    0.320000  0.340000  0.240000  0.339623  0.826087       NaN  0.914894   
6    0.361702  0.300000  0.224490  0.301887  0.744681  0.914894       NaN   
7    0.291667  0.400000  0.208333  0.340000  0.632653  0.795918  0.755102   
8    0.229167  0.276596  0.145833  0.280000  0.509804  0.666667  0.627451   
9    0.295455  0.234043  0.261905  0.347826  0.442308  0.537037  0.500000   
10   0.195122  0.282051  0.250000  0.350000  0.340000  0.442308  0.377358   
11   0.270270  0.454545  0.194444  0.368421  0.354167  0.377358  0.339623   
12   0.342857  0.411765  0.264706  0.368421  0.444444  0.431373  0.420000   
13   0.405405  0.394737  0.263158  0.390244  0.555556  0.500000  0.490196   
14   0.307692  0.405405  0.175000  0.400000  0.500000  0.509804  0.500000   
15   0.285714  0.279070  0.219512  0.340909  0.469388  0.600000  0.625000   
16   0.225806  0.147059  0.214286  0.194444  0.272727  0.280000  0.265306   
17   0.193548  0.407407  0.137931  0.200000  0.279070  0.260000  0.270833   
18   0.250000  0.384615  0.107143  0.250000  0.292683  0.244898  0.282609   
19   0.321429  0.055556  0.375000  0.200000  0.250000  0.260000  0.244898   
20   0.333333  0.423077  0.142857  0.281250  0.200000  0.192308  0.200000   
21   0.310345  0.218750  0.259259  0.343750  0.244444  0.254902  0.215686   
22   0.233333  0.407407  0.100000  0.166667  0.279070  0.285714  0.270833   
23   0.258065  0.428571  0.060606  0.222222  0.266667  0.250000  0.285714   
24   0.296296  0.333333  0.107143  0.212121  0.204545  0.244898  0.255319   
25   0.320000  0.133333  0.260870  0.151515  0.159091  0.180000  0.212766   
26   0.339286  0.381818  0.267857  0.428571  0.660714  0.803571  0.767857   
27   0.233333  0.357143  0.222222  0.235294  0.250000  0.235294  0.244898   
28   0.250000  0.200000  0.291667  0.142857  0.261905  0.297872  0.311111   
29   0.458333  0.161290  0.291667  0.212121  0.292683  0.270833  0.255319   
30   0.241379  0.275862  0.230769  0.205882  0.227273  0.215686  0.250000   
31   0.161290  0.193548  0.230769  0.138889  0.255814  0.240000  0.200000   
32   0.351852  0.396226  0.277778  0.418182  0.716981  0.833333  0.796296   
33   0.206897  0.333333  0.107143  0.212121  0.232558  0.220000  0.204082   
34   0.333333  0.057143  0.280000  0.205882  0.285714  0.265306  0.276596   
35   0.370370  0.266667  0.320000  0.200000  0.279070  0.260000  0.297872   
36   0.230769  0.064516  0.272727  0.121212  0.219512  0.234043  0.244444   
37   0.370370  0.357143  0.137931  0.200000  0.250000  0.235294  0.270833   
38   0.370370  0.407407  0.269231  0.312500  0.222222  0.211538  0.220000   
39   0.333333  0.541667  0.066667  0.205882  0.285714  0.265306  0.276596   
40   0.233333  0.310345  0.178571  0.200000  0.250000  0.260000  0.244898   
41   0.166667  0.384615  0.148148  0.250000  0.204545  0.196078  0.204082   
42   0.117647  0.300000  0.133333  0.264706  0.244444  0.254902  0.240000   
43   0.233333  0.225806  0.269231  0.312500  0.309524  0.312500  0.297872   
44   0.250000  0.333333  0.068966  0.176471  0.152174  0.150943  0.156863   
45   0.333333  0.222222  0.272727  0.121212  0.219512  0.260870  0.244444   
46   0.241379  0.121212  0.391304  0.138889  0.255814  0.265306  0.276596   
47   0.444444  0.250000  0.521739  0.222222  0.266667  0.274510  0.312500   
48   0.259259  0.129032  0.304348  0.258065  0.209302  0.200000  0.208333   
49   0.321429  0.225806  0.375000  0.272727  0.279070  0.235294  0.220000   
50   0.250000  0.125000  0.240000  0.290323  0.204545  0.220000  0.204082   
51   0

In [20]:
rows = [] #list untuk menyimpan data
students = df.index #mengambil index dari dataframe
for i in range(len(students)):
    row_data = [] #list untuk menyimpan data pada baris
    for j in range(len(students)):
        student1 = students[i]
        student2 = students[j]
        if student1 == student2:
            similarity = np.nan #similarity antara student dengan dirinya sendiri adalah NaN
        else: 
            similarity = calculate_URP_similarity(student1, student2)
        row_data.append(similarity)
    rows.append(row_data)

df_urp = pd.DataFrame(rows)
df_urp.columns = students 
df_urp.index = students

df_urp

0         1         2         3         4         5         6    \
0         NaN  0.478897  0.367146  0.474454  0.202010  0.042628  0.080716   
1    0.478897       NaN  0.465731  0.466193  0.347163  0.135379  0.218355   
2    0.367146  0.465731       NaN  0.366920  0.434808  0.202634  0.317767   
3    0.474454  0.466193  0.366920       NaN  0.326901  0.113424  0.181673   
4    0.202010  0.347163  0.434808  0.326901       NaN  0.420893  0.472574   
5    0.042628  0.135379  0.202634  0.113424  0.420893       NaN  0.490022   
6    0.080716  0.218355  0.317767  0.181673  0.472574  0.490022       NaN   
7    0.146058  0.317152  0.434645  0.270791  0.497495  0.453199  0.486681   
8    0.309578  0.454146  0.292119  0.440887  0.462639  0.360608  0.424491   
9    0.350195  0.453049  0.307462  0.460876  0.496734  0.296787  0.370201   
10   0.469599  0.410798  0.279800  0.487016  0.367918  0.132690  0.202951   
11   0.474077  0.454289  0.345706  0.499100  0.327426  0.111261  0.178103   
12   0.453910  0.499312  0.434856  0.498271  0.393006  0.182426  0.267638   
13   0.359730  0.449393  0.485415  0.452982  0.470489  0.303751  0.387453   
14   0.476220  0.372005  0.231023  0.469635  0.403744  0.151998  0.225317   
15   0.365337  0.488870  0.370547  0.459182  0.459022  0.260931  0.339226   
16   0.487306  0.491003  0.436888  0.486645  0.218487  0.052699  0.098735   
17   0.215898  0.337343  0.468295  0.183390  0.206143  0.286901  0.200348   
18   0.428145  0.490922  0.495559  0.454958  0.273805  0.081482  0.148621   
19   0.456619  0.489431  0.475925  0.477325  0.263811  0.076531  0.138462   
20   0.486849  0.476237  0.452203  0.472496  0.185013  0.039166  0.076844   
21   0.482326  0.490442  0.445795  0.494529  0.231178  0.058960  0.109078   
22   0.286569  0.403275  0.490539  0.265744  0.366261  0.447001  0.419300   
23   0.463941  0.494816  0.468105  0.474311  0.287186  0.090617  0.158494   
24   0.358514  0.463204  0.499919  0.362181  0.429870  0.195843  0.310820   
25   0.140373  0.261443  0.410853  0.120701  0.141332  0.196377  0.130162   
26   0.039344  0.068804  0.056077  0.108290  0.484977  0.301754  0.316721   
27   0.302301  0.414001  0.495536  0.279342  0.379812  0.431406  0.435792   
28   0.412955  0.497391  0.496858  0.430611  0.317559  0.108312  0.189303   
29   0.123555  0.239195  0.395432  0.103506  0.112747  0.147400  0.097214   
30   0.322571  0.434209  0.496517  0.313016  0.468132  0.306150  0.440087   
31   0.447184  0.490523  0.482890  0.468235  0.272200  0.081172  0.146329   
32   0.023578  0.040433  0.028301  0.074558  0.471562  0.248007  0.276151   
33   0.141831  0.260372  0.414723  0.117837  0.125548  0.163531  0.109302   
34   0.325793  0.434937  0.497484  0.313439  0.460289  0.317967  0.451728   
35   0.328867  0.433604  0.500000  0.308915  0.431263  0.360957  0.494052   
36   0.185496  0.318340  0.443105  0.173125  0.249465  0.392313  0.271732   
37   0.290568  0.407031  0.491188  0.271356  0.379471  0.426716  0.438063   
38   0.223242  0.345226  0.470560  0.192708  0.225928  0.322643  0.226711   
39   0.199308  0.322130  0.457822  0.169536  0.191850  0.266940  0.184392   
40   0.325152  0.430417  0.500000  0.303398  0.418096  0.379577  0.487445   
41   0.201425  0.329718  0.454210  0.181680  0.239777  0.362909  0.252733   
42   0.314832  0.419815  0.497459  0.283291  0.360244  0.470327  0.403447   
43   0.279061  0.394369  0.491161  0.251016  0.322582  0.479557  0.355510   
44   0.109934  0.217765  0.384419  0.086595  0.079174  0.089628  0.060077   
45   0.227799  0.363769  0.466527  0.222083  0.349200  0.446786  0.409003   
46   0.383094  0.474038  0.499455  0.383017  0.414782  0.185499  0.294687   
47   0.447355  0.497959  0.482475  0.445670  0.345409  0.131819  0.217596   
48   0.334116  0.449120  0.498369  0.337973  0.459274  0.221210  0.344720   
49   0.271547  0.387258  0.490187  0.240664  0.298674  0.438943  0.321508   
50   0.356779  0.459394  0.499778  0.355383  0.452417  0.219076  0.338778   
51   0

In [21]:

rating_student_u = df.loc[2]
rating_student_v = df.loc[3]

items_u = set(rating_student_u.index[rating_student_u > 0]) #Memilih item yang pernah di nilai oleh user u
items_v = set(rating_student_v.index[rating_student_v > 0]) #Memilih item yang pernah di nilai oleh user v
intersection = len(items_u.intersection(items_v))
union = len(items_u.union(items_v))

print(intersection)
print(union)

print (intersection/union)


7
34
0.20588235294117646


In [22]:
rating_student_u = df.loc[2]
rating_student_v = df.loc[3]
    
mean_student_u = statistics.mean(rating_student_u)
mean_student_v = statistics.mean(rating_student_v)
    
var_student_u = statistics.variance(rating_student_u)
var_student_v = statistics.variance(rating_student_v)


print("mean student u :",mean_student_u)
print("mean student v :",mean_student_v)
print("variance student u :",var_student_u)
print("variance student v :",var_student_v)

print(1-(1/(1+math.exp(-abs(mean_student_u-mean_student_v)*abs(var_student_u-var_student_v)))))

mean student u : 1.1428571428571428
mean student v : 1.8571428571428572
variance student u : 3.651948051948052
variance student v : 4.415584415584416
0.36691963074516754


In [23]:
rows = [] #list untuk menyimpan data
students = df.index #mengambil index dari dataframe
for i in range(len(students)):
    row_data = [] #list untuk menyimpan data pada baris
    for j in range(len(students)):
        student1 = students[i]
        student2 = students[j]
        if student1 == student2:
            similarity = np.nan #similarity antara student dengan dirinya sendiri adalah NaN
        else: 
            similarity =(calculate_PSS_similarity(student1, student2))*(calculate_Jaccard_similarity(student1, student2))*(calculate_URP_similarity(student1, student2))
        row_data.append(similarity)
    rows.append(row_data)


df_sim = pd.DataFrame(rows)
df_sim.columns = students 
df_sim.index = students

df_sim

0         1         2         3         4         5         6    \
0         NaN  0.652923  0.720841  0.466405  0.124066  0.016242  0.047884   
1    0.652923       NaN  0.390061  0.502604  0.291967  0.048210  0.068764   
2    0.720841  0.390061       NaN  0.272995  0.214265  0.053683  0.094006   
3    0.466405  0.502604  0.272995       NaN  0.152074  0.026446  0.041952   
4    0.124066  0.291967  0.214265  0.152074       NaN  0.559485  0.573729   
5    0.016242  0.048210  0.053683  0.026446  0.559485       NaN  0.666895   
6    0.047884  0.068764  0.094006  0.041952  0.573729  0.666895       NaN   
7    0.061625  0.226589  0.129285  0.113047  0.403664  0.480393  0.460265   
8    0.104692  0.189149  0.059288  0.160053  0.191982  0.203240  0.221753   
9    0.238008  0.203079  0.182216  0.302180  0.186357  0.107548  0.130836   
10   0.222232  0.309545  0.221282  0.413828  0.147647  0.046711  0.058397   
11   0.395137  0.759249  0.229149  0.505932  0.188889  0.032477  0.048417   
12   0.546003  0.760612  0.433653  0.528542  0.385598  0.089900  0.140067   
13   0.473550  0.531674  0.396106  0.446761  0.584784  0.146814  0.228772   
14   0.410812  0.438134  0.109087  0.494169  0.333539  0.061522  0.122620   
15   0.230397  0.262565  0.189988  0.299474  0.227111  0.160981  0.281128   
16   0.483536  0.284293  0.445718  0.334147  0.134923  0.018391  0.036909   
17   0.194211  0.693763  0.319166  0.139968  0.137044  0.088458  0.081764   
18   0.503616  0.918588  0.255142  0.447080  0.189456  0.022002  0.062480   
19   0.704015  0.101081  0.958697  0.344839  0.144009  0.022811  0.044420   
20   0.793163  1.011650  0.310074  0.517873  0.079667  0.007197  0.019133   
21   0.695086  0.448068  0.574848  0.672147  0.113087  0.014798  0.025802   
22   0.308559  0.794593  0.225207  0.153775  0.228214  0.164014  0.164558   
23   0.528426  0.996850  0.120788  0.367748  0.160019  0.020302  0.059678   
24   0.501677  0.701607  0.252709  0.285253  0.173876  0.050545  0.105348   
25   0.237988  0.161219  0.594655  0.069494  0.051066  0.046447  0.046543   
26   0.024232  0.056168  0.029250  0.078335  0.411784  0.164418  0.175578   
27   0.330805  0.708206  0.557754  0.248209  0.206232  0.104297  0.137951   
28   0.482277  0.425556  0.766759  0.215535  0.187588  0.042594  0.095733   
29   0.304678  0.172352  0.651230  0.087552  0.085072  0.058457  0.041983   
30   0.371235  0.560269  0.581858  0.240614  0.237261  0.074417  0.170440   
31   0.304693  0.399004  0.547505  0.208673  0.159305  0.023644  0.037145   
32   0.014317  0.024633  0.015443  0.037843  0.475945  0.199086  0.217827   
33   0.135641  0.414558  0.220540  0.095071  0.067630  0.039784  0.029512   
34   0.550556  0.098626  0.743251  0.243786  0.331639  0.114985  0.208101   
35   0.601170  0.522695  0.826934  0.217067  0.293643  0.117288  0.245409   
36   0.213741  0.084586  0.664313  0.076776  0.130181  0.119414  0.106882   
37   0.549398  0.743525  0.342830  0.207149  0.225489  0.117417  0.188208   
38   0.408699  0.701697  0.660474  0.242735  0.115892  0.077221  0.071572   
39   0.322232  0.906574  0.140400  0.127169  0.132221  0.086150  0.075031   
40   0.334514  0.588216  0.420506  0.211668  0.208160  0.102036  0.144522   
41   0.152960  0.618996  0.337702  0.179553  0.096972  0.061126  0.061862   
42   0.141608  0.536830  0.295424  0.272368  0.160775  0.104190  0.106644   
43   0.284256  0.373998  0.650283  0.298081  0.246361  0.212178  0.175012   
44   0.129023  0.344098  0.126187  0.056495  0.022078  0.008688  0.008888   
45   0.396448  0.376555  0.712475  0.099930  0.186448  0.174716  0.170734   
46   0.434340  0.236901  1.068357  0.182947  0.248551  0.066842  0.133212   
47   1.009740  0.535374  1.403308  0.338787  0.203328  0.042178  0.106569   
48   0.429375  0.256107  0.849421  0.361131  0.233722  0.052307  0.106047   
49   0.417549  0.378966  0.992239  0.250244  0.204613  0.121281  0.094605   
50   0.411053  0.232388  0.608474  0.415848  0.187957  0.051112  0.089155   
51   0

In [24]:
NIM_Mahasiswa = input("Masukkan NIM Mahasiswa yang ingin direkomendasikan: ")

if NIM_Mahasiswa in df_raw['ID'].to_list():
    
    student_want_recommendation = df_raw['ID'].to_list().index(NIM_Mahasiswa)
    sort_sim = df_sim[student_want_recommendation].sort_values(ascending=False)
    sort_sim = sort_sim.head(50)

    item_rated_high_sim = []
    recommended_items = []
    for i in range(len(df_sim)):
        highest_sim = sort_sim.index.to_list()[i:i+1]
        item_not_rated = df_2.loc[student_want_recommendation][df_2.loc[student_want_recommendation] == 0].index.to_list()
        item_rated = df_2.loc[student_want_recommendation][df_2.loc[student_want_recommendation] != 0].index.to_list()
    
        for j in range(len(highest_sim)):
            items = df_2.loc[highest_sim[j]][df_2.loc[highest_sim[j]] > 0].index.to_list()
            item_rated_high_sim.extend(items)

            recommended = set(item_rated_high_sim).intersection(item_not_rated)
            recommended_items.extend(recommended)
            

    print(sort_sim)
    # print(highest_sim)
    # print(item_rated)
    # print(item_not_rated)
    # print(item_rated_high_sim)
    recommended = list(OrderedDict.fromkeys(recommended_items))
else:
    print("NIM mahasiswa tidak ditemukan")



100    4.010704
147    2.653355
125    2.643690
122    2.643690
150    2.615625
126    1.996326
107    1.987877
124    1.978512
104    1.971766
117    1.969865
113    1.968721
95     1.949778
112    1.930176
120    1.572917
110    1.566931
99     1.566102
127    1.556483
141    1.519618
151    1.492460
103    1.471991
98     1.290102
78     1.276439
106    1.259647
65     1.130897
74     1.096864
91     0.784306
97     0.764684
89     0.764599
92     0.634973
60     0.604337
62     0.505596
29     0.355785
55     0.348666
59     0.335123
68     0.324735
61     0.306481
85     0.295719
71     0.276795
25     0.238000
51     0.196245
57     0.183907
87     0.141244
49     0.135227
38     0.114626
72     0.111142
50     0.080261
37     0.076394
43     0.076288
56     0.073843
48     0.070056
Name: 94, dtype: float64


In [25]:
#print df raw kolom nama loc 3
print(df_raw.loc[20]['Nama'])
print(df_raw.loc[23]['Nama'])
print(df_raw.loc[18]['Nama'])
print(df_raw.loc[39]['Nama'])
print(df_raw.loc[22]['Nama'])

print(df_raw.loc[19]['Nama'])
print(df_raw.loc[21]['Nama'])
print(df_raw.loc[1]['Nama'])
print(df_raw.loc[115]['Nama'])
print(df_raw.loc[35]['Nama'])

print(df_raw.loc[34]['Nama'])
print(df_raw.loc[37]['Nama'])
print(df_raw.loc[12]['Nama'])
print(df_raw.loc[23]['Nama'])
print(df_raw.loc[18]['Nama'])

print(df_raw.loc[9]['Nama'])

Responden21
Responden24
Responden19
Responden40
Responden23
Responden20
Responden22
Responden2
Responden116
Responden36
Responden35
Responden38
Responden13
Responden24
Responden19
Responden10


In [26]:
df_recommended = pd.DataFrame({'Items Recommended': recommended})


df_recommended


Items Recommended
0                                   Teori Pengkodean 
1                                  Sistem Basis Data 
2                              Matematika Keuangan 1 
3                                  Teori Grup Hingga 
4                            Aplikasi Aljabar Linear 
5                               Pengantar Teori Graf 
6                        Praktikum Sistem Basis Data 
7                                     Aljabar Linear 
8                   Pengantar Sistem Dinamik Diskret 
9                      Matematika Ekonomi dan Bisnis 
10                     Pengantar Pemodelan Gelombang 
11                     Pengantar Diferensial Numerik 
12                                     Kombinatorika 
13  Praktikum Pengantar Pengantar Diferensial Nume...
14                                  Kalkulus Variasi 
15                             Persamaan Beda Hingga 
16                     Pengantar Pemodelan Stokastik 
17                                  Pengantar Fisika 
18                                     Teori Bilangan
19                                 Pengantar Biologi 
20                                   Riset Operasi 2 
21                        Praktikum Optimasi Numerik 
22                             Pengantar Data Mining 
23                                  Optimasi Numerik 
24              Praktikum Pengantar Komputasi Cerdas 
25                        Pengantar Komputasi Cerdas 
26                             Matematika Asuransi 1 
27                  Pengantar Sistem Dinamik Kontinu 
28                       Pengantar Dinamika Populasi 
29                Pengantar Pengolahan Citra Digital 
30                                     Fungsi Khusus 
31                                   Teori Permainan 
32      Praktikum Pengantar Pengolahan Citra Digital 
33                      Pengantar Optimasi Heuristik 
34                    Pengantar Geometri Diferensial 
35                   Pengantar Analisis Reliabilitas 
36                             Matematika Keuangan 2 
37                             Matematika Asuransi 2 
38                             Pengantar Teori Modul 
39                        Pengantar Metode Peramalan 
40                  Pengantar Fungsi Kontrol Optimal 
41                          Pengantar Regresi Linear 
42                         Pengantar Fungsi Univalen

In [27]:
df_recommended.to_csv('D:\\SKRIPSI\\Code\\matkulrekomendasi.csv')